In [1]:
import pandas as pd
import tensorflow as tf

import autokeras as ak

from settings import INPUT_FILE, CORR_GROUP, OUTPUT_FILE
import numpy as np
from sklearn.preprocessing import MinMaxScaler
import logging


2022-09-11 12:34:41.778201: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-09-11 12:34:41.778278: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.


In [2]:
def unique_cols(df):
    a = df.to_numpy() # df.values (pandas<0.24)
    return (a[0] == a).all(0)

def create_supervised_dataset(df, target, feats, n_in=1, n_out=1):
    cols, names = list(), list()
    n_vars = len(feats)
    # input sequence (t-n, ... t-1)
    for i in range(n_in, 0, -1):
        cols.append(df[feats].shift(i))
        names += [('var%d(t-%d)' % (j+1, i)) for j in range(n_vars)]
    # forecast sequence (t, t+1, ... t+n)
    for i in range(0, n_out):
        cols.append(df[target].shift(-i))
        if i == 0:
            names += [('var%d(t)' % (j+1)) for j in range(1)]
        else:
            names += [('var%d(t+%d)' % (j+1, i)) for j in range(1)]
    # put it all together
    agg = pd.concat(cols, axis=1)
    agg.columns = names
    agg.dropna(inplace=True)
    return agg.values

In [3]:
df = pd.read_csv(INPUT_FILE, index_col='ts')
#df = df.drop('Unnamed: 0', 1)
df.index = pd.to_datetime(df.index)

df_2 = df.loc[:,np.invert(unique_cols(df))]
# Average window
# df_2 = df.groupby(np.arange(len(df))//60).mean()

scaler = MinMaxScaler()
d = scaler.fit_transform(df_2)
scaled_df = pd.DataFrame(d, columns=df_2.columns, index=df_2.index)
results = []
train_split = int(0.7*scaled_df.shape[0])
val_split = int(0.9*scaled_df.shape[0])
predict_from = 1
predict_until = 1
lookback = 15

In [4]:
for k in CORR_GROUP:
    scaled_df['AD'] = " "
    scaled_df[k + ' Control'] = " "
scaled_df.head()

AE_L1  AE_L2         AE_L3  AE_SUM  C_phi_L1  C_phi_L2  \
ts                                                                            
2022-04-14 09:45:00    0.0    0.0  0.000000e+00     0.0       0.0       0.0   
2022-04-14 09:46:00    0.0    0.0  0.000000e+00     0.0       0.0       0.0   
2022-04-14 09:47:00    0.0    0.0  4.502219e-07     0.0       0.0       0.0   
2022-04-14 09:48:00    0.0    0.0  4.911512e-07     0.0       0.0       0.0   
2022-04-14 09:49:00    0.0    0.0  7.530985e-07     0.0       0.0       0.0   

                     C_phi_L3         F  H_TDH_I_L1_N  H_TDH_I_L2_N  ...  \
ts                                                                   ...   
2022-04-14 09:45:00  0.985689  0.591371      0.878465      0.769139  ...   
2022-04-14 09:46:00  0.836782  0.632546      0.878465      0.769139  ...   
2022-04-14 09:47:00  0.820093  0.603675      0.878465      0.769139  ...   
2022-04-14 09:48:00  0.739987  0.597113      0.878465      0.769139  ...   
2022-04-14 09:49:00  0.756175  0.536745      0.878465      0.769139  ...   

                     P_SUM Control  U_L1_N Control  I_SUM Control  \
ts                                                                  
2022-04-14 09:45:00                                                 
2022-04-14 09:46:00                                                 
2022-04-14 09:47:00                                                 
2022-04-14 09:48:00                                                 
2022-04-14 09:49:00                                                 

                     H_TDH_I_L3_N Control  F Control  ReacEc_L1 Control  \
ts                                                                        
2022-04-14 09:45:00                                                       
2022-04-14 09:46:00                                                       
2022-04-14 09:47:00                                                       
2022-04-14 09:48:00                                                       
2022-04-14 09:49:00                                                       

                     C_phi_L3 Control  ReacEc_L3 Control  RealE_SUM Control  \
ts                                                                            
2022-04-14 09:45:00                                                           
2022-04-14 09:46:00                                                           
2022-04-14 09:47:00                                                           
2022-04-14 09:48:00                                                           
2022-04-14 09:49:00                                                           

                     H_TDH_U_L2_N Control  
ts                                         
2022-04-14 09:45:00                        
2022-04-14 09:46:00                        
2022-04-14 09:47:00                        
2022-04-14 09:48:00                        
2022-04-14 09:49:00                        

[5 rows x 67 columns]

In [5]:
train_split = int(0.7*scaled_df.shape[0])
val_split = int(0.9*scaled_df.shape[0])
data_train = scaled_df[:train_split]
data_cv = scaled_df[train_split:val_split]

for k in CORR_GROUP:
    data_test = create_supervised_dataset(scaled_df, k, CORR_GROUP[k], n_in=lookback, n_out=1)[val_split:]
    data_x_test, data_y_test = data_test[:, :-1], data_test[:, -1]
    data_x_test = data_x_test.reshape(-1, lookback, len(CORR_GROUP[k]))
    print(data_x_test.shape)
    print(data_y_test.shape)
    model = tf.keras.models.load_model(f'models/{k}_autokeras.h5')
    scaled_df[k + ' Control'].iloc[val_split+15:] = model.predict(data_x_test).reshape(-1)

(3941, 15, 19)
(3941,)


2022-09-11 12:34:51.991765: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcuda.so.1'; dlerror: libcuda.so.1: cannot open shared object file: No such file or directory
2022-09-11 12:34:51.991891: W tensorflow/stream_executor/cuda/cuda_driver.cc:269] failed call to cuInit: UNKNOWN ERROR (303)
2022-09-11 12:34:51.991951: I tensorflow/stream_executor/cuda/cuda_diagnostics.cc:156] kernel driver does not appear to be running on this host (semantic): /proc/driver/nvidia/version does not exist
2022-09-11 12:34:51.992679: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


124/124 [==============================] - 3s 7ms/step


/tmp/ipykernel_1461544/1156096480.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  scaled_df[k + ' Control'].iloc[val_split+15:] = model.predict(data_x_test).reshape(-1)


(3941, 15, 6)
(3941,)
124/124 [==============================] - 3s 5ms/step
(3941, 15, 1)
(3941,)


...

/tmp/ipykernel_1461544/1156096480.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  scaled_df[k + ' Control'].iloc[val_split+15:] = model.predict(data_x_test).reshape(-1)


(3941, 15, 21)
(3941,)
124/124 [==============================] - 3s 6ms/step
(3941, 15, 3)
(3941,)


/tmp/ipykernel_1461544/1156096480.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  scaled_df[k + ' Control'].iloc[val_split+15:] = model.predict(data_x_test).reshape(-1)


124/124 [==============================] - 2s 5ms/step


/tmp/ipykernel_1461544/1156096480.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  scaled_df[k + ' Control'].iloc[val_split+15:] = model.predict(data_x_test).reshape(-1)


In [19]:
import plotly.express as px
for k in CORR_GROUP:
    df2 = scaled_df.iloc[val_split+15:][[k, k+' Control']]
    df2[k + ' Control'] = df2[k + ' Control'].astype(float)
    fig = px.line(df2, x=df2.index, y=df2.columns, height=800, title=k + ' Control')
    fig.show()